In [120]:
import json
import psycopg2
from datetime import datetime
import time

In [95]:
def connect_to_postgres_database(db_name):
    try:
        conn = psycopg2.connect(
            dbname=db_name, 
            user='postgres', 
            password='king', 
            host='localhost'
        )
        conn.autocommit = True
        cursor = conn.cursor()
        print(f"Connected to PostgreSQL db {db_name}")
        return conn, cursor
    except Exception as e:
        print("An error occurred while connecting: ", e)

In [96]:
def create_database(cursor, db_name):
    try:
        cursor.execute(f'CREATE DATABASE "{db_name}"')
        print(f"Database {db_name} created successfully")
    except Exception as e:
        print("An error occurred while creating the database: ", e)

In [103]:
def create_table(cursor):
    try:
        cursor.execute("""
            CREATE TABLE IF NOT EXISTS users (
                id VARCHAR(255) PRIMARY KEY,
                name VARCHAR(255),
                screen_name VARCHAR(255),
                verified BOOLEAN,
                location VARCHAR(255),
                description VARCHAR(255),
                followers_count BIGINT,
                friends_count BIGINT, 
                favourites_count BIGINT,
                statuses_count BIGINT,
                created_at TIMESTAMP
            )
            """)
        conn.commit()
        print("Table 'users' created successfully")
    except Exception as e:
        print("An error occurred while creating the table: ", e)

In [98]:
conn, cursor = connect_to_postgres_database('postgres')

Connected to PostgreSQL db postgres


In [99]:
create_database(cursor, 'twitter-database')

Database twitter-database created successfully


In [100]:
# Close the previous connection and connect to the new database
conn.close()
conn, cursor = connect_to_postgres_database('twitter-database')

Connected to PostgreSQL db twitter-database


In [110]:
create_table(cursor)

Table 'users' created successfully


In [105]:
class User(object):
    
    def __init__(self, user):
        self.id = user['id_str']
        self.name = user['name']
        self.screen_name = user['screen_name']
        self.verified = user['verified']
        self.location = user['location']
        self.description = user['description']
        self.followers_count = user['followers_count']
        self.friends_count = user['friends_count']
        self.favourites_count = user['favourites_count']
        self.statuses_count = user['statuses_count']
        self.created_at = self.get_created_date(user['created_at'])
    
    @staticmethod    
    def get_created_date(created_at):
        created_at_date = datetime.strptime(created_at, "%a %b %d %H:%M:%S %z %Y")
        created_at_date = created_at_date.strftime("%Y-%m-%d %H:%M:%S")
        return created_at_date
        
    def get_user(self):
        return (self.id, self.name, self.screen_name, self.verified, self.location, self.description,
                self.followers_count, self.friends_count, self.favourites_count, self.statuses_count, self.created_at)
    
    

In [106]:
def insert_user(cursor, user):
    try:
        cursor.execute("""
            INSERT INTO users (id, name, screen_name, verified, location, description, followers_count, friends_count, favourites_count, statuses_count, created_at)
            VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
        """, user)
        conn.commit()
        print("User inserted into table successfully")
    except Exception as e:
        print("An error occurred while inserting data: ", e)

In [24]:
# Insert a sample user
# user = ('1242817830946508801', 'juwelz v', 'juwelz_v', False, 'Lower East Side, Manhattan', 'Event Lyfe LLC .. Brand Ambassador: #visionarysociety Music Manager: @ssizzzlee & @tmoneybeatsbang Production🎥📸 #BringNyCultureBack 🌊🌊🌊 !!', 43, 118, 722, 906, '2020-03-25 14:17:28')
# insert_user(cursor, user)

User inserted into table successfully


In [122]:
def load_user_data_to_database(db_cursor, file_path, users):
    
    start_time = time.time()
    user_count = 0
    
    with open(file_path, "r") as file:
        for line in file:
            try:
                data = json.loads(line)
                user = data['user']
                
                if user['id_str'] not in users:
                    users.add(user['id_str'])
                    user_count += 1
                    user_object = User(user)
                    if user_count <= 100:
                        print(user_object.get_user())
                    insert_user(db_cursor, user_object.get_user())
                    print(f"Inserted users: {user_count}")      
            except:
                continue
    
    print(f"Successfully inserted {user_count} users in {time.time() - start_time} seconds")

In [123]:
users = set()

In [124]:
load_user_data_to_database(cursor, "/Users/sasankchindirala/PycharmProjects/dbms-project/dbms-stat694-sp2024-team31/data-curation-application/data/corona-out-2", users)

('1242817830946508801', 'juwelz v', 'juwelz_v', False, 'Lower East Side, Manhattan', 'Event Lyfe LLC .. Brand Ambassador: #visionarysociety Music Manager: @ssizzzlee & @tmoneybeatsbang Production🎥📸 #BringNyCultureBack 🌊🌊🌊 !!', 43, 118, 722, 906, '2020-03-25 14:17:28')
User inserted into table successfully
Inserted users: 1
('1225145123920588805', 'efe09', 'efe0927183508', False, None, "Allah'ın en değerli eseri insandır.\nCanı yanan sabretsin.\nCan yakan, canının yanacağı günü beklesin..\n677 khk\nRT düşüncem olduğu anlamına gelmez bilgi amaçlıdır", 653, 983, 1255, 4177, '2020-02-05 19:52:38')
User inserted into table successfully
Inserted users: 2
('101007632', 'Ravin Gupta', 'IamRaavin', False, 'india', 'Tweet is personal opinion and Retweet is not endorsement.', 499, 537, 4342, 4038, '2010-01-01 16:24:24')
User inserted into table successfully
Inserted users: 3
('1230170166614482944', 'Carpe diem', 'Carpedi92670638', False, None, 'Yezidin hârcı zulüm\nYiğidin burcu ölüm', 425, 459, 

In [125]:
load_user_data_to_database(cursor, "/Users/sasankchindirala/PycharmProjects/dbms-project/dbms-stat694-sp2024-team31/data-curation-application/data/corona-out-3", users)

('804046791348015107', 'Bi Sex Uau', 'B_King69', False, 'Acre, Brasil', 'se for da minha família já pode voltar daq mesmo', 89, 173, 5446, 4728, '2016-11-30 19:37:48')
User inserted into table successfully
Inserted users: 1
('2242948745', 'Thomas Krause', 'tho1965', False, None, 'Sportredakteur @nordkurier 🏃\u200d♂️🚴\u200d♂️⚽️', 173, 685, 2184, 1865, '2013-12-25 09:13:33')
User inserted into table successfully
Inserted users: 2
('908326492718764034', 'शचीन्द्र पाण्डेय', 'im_S_pandey', False, 'Amethi Uttar Pradesh', 'Official Twitter Handel Shachindra Pandey (@im_s_pandey) BJP IT Department Amethi District\n Fallow by Narendra Modi \n (@narendramodi) ji', 2362, 202, 30668, 48906, '2017-09-14 13:48:06')
User inserted into table successfully
Inserted users: 3
('2929344220', 'Ralf Schmitz', 'RusticusArat', False, '🇩4790 Provinz ', 'BWLer,ex Offz,Tw meistens zwischen Tür & Angel. \nGender* sind eine Zumutung\n\nRT ≠ endorsement', 778, 733, 32024, 30551, '2014-12-18 10:19:26')
User inserted 